# PACBED from SPED data labeled by ASTAR
* 2022-01-18 Alex initial version 
* 2022-05-03 Alex edit for export <br><br>

In [ ]:
import pandas as pd
import numpy as np
#import pickle
import matplotlib.pyplot as plt
import matplotlib.colors as colors
import hyperspy.api as hs
#import pyxem as pxm
import cv2
from tqdm import tqdm
import gc

In [ ]:
# load ASTAR ACOM results
df = pd.read_csv("21-08-23_5e12_wCUBIC.ang",
                    delim_whitespace=True,
                    comment='#', #this skips comment lines
                    names=["ex","ey","ez","pxx","pxy","u1","u2","phase","u3"]
                    )
# some references for the *.ang file format
# http://www.dream3d.io/Filters/OrientationAnalysisFilters/ReadAngData/

In [ ]:
# export data in *.hdf5 file, here the hyperspy format is used
s.save("./HfO2_ion_beam_irradiated_5e12ions-per-cm2.hspy")

In [ ]:
s = hs.load("./HfO2_ion_beam_irradiated_5e12ions-per-cm2.hspy", lazy=True)
print(s.axes_manager[0].size*s.axes_manager[1].size)

In [ ]:
# crop here, if necessary
#s = s.inav[:,100:110]
df = df.truncate(before=75*s.axes_manager[0].size,after=225*s.axes_manager[0].size-1)
print(s.axes_manager[0].size*s.axes_manager[1].size,len(df))

In [ ]:
# check if the *.ang file was loaded correctly
print(len(df))
# print the header 
df.head()

In [ ]:
# scale to pixel scale
scale = df["pxx"][1:].values[0]
print("scale: "+str(scale))

dfpxscale = df[["pxx","pxy"]].div(scale) # divide by scale
df["pxx"] = dfpxscale["pxx"]
df["pxy"] = dfpxscale["pxy"]
print(len(df))
df.head()

In [ ]:
# reshape list into 2D image, pixel positions are given in table
array = df[["pxx","pxy","phase"]].values
print(array.shape)
xstart = df["pxx"].min()
xstop = df["pxx"].max()
ystart = df["pxy"].min()
ystop = df["pxy"].max()
x = xstop - xstart
y = ystop - ystart + 1 # why plus one here?
print(x,y,(x+1)*(y+1))
test1reshape = np.reshape(array[:,2], (int(y+1),int(x+1)))
print(test1reshape.shape)

In [ ]:
# euler angles
df[df[["ex","ey","ez","phase"]]["phase"].isin([1])]


In [ ]:
# let's plot an "ACOM map"
phases = ["Pt","Si","c-HfO2-x","m-HfO2","amorphous"]
plt.figure(figsize = (16,6))
plt.imshow(test1reshape, cmap="tab10_r")
plt.legend(labels=["1","2","3","4","5"],fontsize="xx-large")

In [ ]:
# general use with pandas object
phases = ["Pt","Si","c-HfO2-x","m-HfO2","amorphous"]
work = df[["pxx","pxy","phase"]] # add columns here
phasespos = [work[work["phase"].isin([1])],
             work[work["phase"].isin([2])],
             work[work["phase"].isin([3])],
             work[work["phase"].isin([4])],
             work[work["phase"].isin([5])]
             ]
phasespos[4].head()

In [ ]:
# display random k-space frames
print(
    len(phasespos[0]["pxx"].values),
    len(phasespos[1]["pxx"].values),
    len(phasespos[2]["pxx"].values),
    len(phasespos[3]["pxx"].values),
    len(phasespos[4]["pxx"].values))
phasenum = 3
#print(len(phasespos[phasenum]["pxx"].values))
rand1 = np.random.randint(low=0, high=len(phasespos[phasenum]["pxx"].values), size=1)
rand2 = np.random.randint(low=0, high=len(phasespos[phasenum]["pxx"].values), size=1)
rand3 = np.random.randint(low=0, high=len(phasespos[phasenum]["pxx"].values), size=1)
#print(rand1,rand2,rand3)
locx1 = int(phasespos[phasenum]["pxx"].values[rand1])
locy1 = int(phasespos[phasenum]["pxy"].values[rand1])
locx2 = int(phasespos[phasenum]["pxx"].values[rand2])
locy2 = int(phasespos[phasenum]["pxy"].values[rand2])
locx3 = int(phasespos[phasenum]["pxx"].values[rand3])
locy3 = int(phasespos[phasenum]["pxy"].values[rand3])
print("(",locx1,locy1,"), (",locx2,locy2,"), (",locx3,locy3,")")
# here, the scaled frame is added --> average
fig, axs = plt.subplots(1,3,figsize=(16, 6))
axs[0].imshow(s.inav[locx1,locy1].data)
axs[1].imshow(s.inav[locx2,locy2].data)
axs[2].imshow(s.inav[locx3,locy3].data)

In [ ]:
# create a dictionary for the phases, names and summed reciprocal space included
phases = ["Pt","Si","c-HfO2-x","m-HfO2","amorphous"]
phasedict = dict(zip(phases, np.zeros_like(s.inav[0,0].data)))
filename = "2022-02-07_results_v18_rand_p"
# if necessary, limit the number of real-space pixels/k-space frames)
randomframesnum = 20000

# here the summing is done for all phases and all pixels that are labeled as the specific phase
for p in range(len(phasedict.items())):
    phasenum = p
    sump = np.zeros((256,256))
    count = 0
    numframes = randomframesnum
    for xx in tqdm(range(randomframesnum)): # this loops over xx random frames from that phase
        if len(phasespos[phasenum]["pxx"].values) == 0:
            count += 1
            continue
        else:
            rand = np.random.randint(low=0, high=len(phasespos[phasenum]["pxx"].values), size=1)
            locx = int(phasespos[phasenum]["pxx"].values[rand])
            locy = int(phasespos[phasenum]["pxy"].values[rand])
            sump = np.add(sump,s.inav[locx,locy].data/numframes)
            count += 1
    print(type(sump),type(np.array(sump)))
    np.save(filename+str(phasenum+1)+".npy",np.array(sump))
    print("file saved, "+str(count)+" frames summed")
    del sump
    gc.collect()
    print("phase "+str(p+1)+" of "+str(len(phasedict.items()))+" done")

In [ ]:
# OpenCV rot average, this could be sped up by using pyxem/pyFAI
def rotavg(array,center=(128,128),radius=128):
    "rotavg, nparray, center=(128,128), radius=128"
    #input: data, center, radius of polar projection
    #get a numpy array
    # init
    awork = array
    output = np.zeros((awork.shape[0],awork.shape[1]))
    # begin
    source = cv2.normalize(src=np.array(awork), dst=None, alpha=0, beta=255, norm_type=cv2.NORM_MINMAX, dtype=cv2.CV_8UC1)
    img = source.astype(np.float32)
    value = np.sqrt(((img.shape[0]/2.0)**2.0)+((img.shape[1]/2.0)**2.0))
    polar_image = cv2.linearPolar(img,center,radius,cv2.WARP_FILL_OUTLIERS)
    polar_image = polar_image.astype(np.uint8)
    # integrate the full image
    output = np.sum(polar_image[:,:],0)

    return output, polar_image

In [ ]:
filename = "2022-02-07_results_v18_rand_"
loaded = [
np.load(filename+"p1.npy"),
np.load(filename+"p2.npy"),
np.load(filename+"p3.npy"),
#np.load(filename+"p4.npy"),
#np.load(filename+"p5.npy")
]

fig, axs = plt.subplots(3,2,figsize=(10,15))
for i in range(3):
    axs[i,0].imshow(rotavg(loaded[i],center=(123,124))[1])
    axs[i,1].plot(rotavg(loaded[i],center=(122,124))[0])
    axs[i,1].set_xlim(25, 240)
    axs[i,1].set_ylim(7000, 20000) 
#fig.savefig(filename+"_rotavg_phases.png")

In [ ]:
phases = ["Pt","Si","c-HfO2-x","m-HfO2","amorphous"]
#plt.plot(rotavg((loaded[2]-loaded[3]),center=(123,124))[0])
plt.plot(rotavg(loaded[1],center=(123,124))[0])
plt.plot(rotavg(loaded[2],center=(123,124))[0])
plt.xlim((25,150))
plt.ylim((9000,20000))
plt.legend([phases[2],[phases[3]]],fontsize="xx-large")
#plt.plot(rotavg(loaded[2],center=(123,124))[0]-rotavg(loaded[3],center=(123,124))[0])